In [2]:
import os
import cv2
import numpy as np
from tqdm import tqdm
from datetime import datetime
from collections import deque
from ultralytics import YOLO

class SwimmerTracker:
    def __init__(self, model_path='yolov8x.pt', conf_thresh=0.6):
        self.model = YOLO(model_path)
        self.model.conf = conf_thresh
        self.model.classes = [0]  # Only 'person' class from COCO

        self.conf_threshold = conf_thresh
        self.tracks = {}
        self.track_gap = 10
        self.track_min_length = 3
        self.track_max_length = 30

        self.pool_hsv_ranges = [
            {'low': np.array([90, 50, 50]), 'high': np.array([130, 255, 255])},
            {'low': np.array([80, 40, 40]), 'high': np.array([100, 255, 255])}
        ]

        self.detection_rules = {
            'aspect': (0.3, 3.0),
            'area': (0.01, 0.4),
            'overlap': 0.3,
            'min_size': (30, 30),
            'vertical_cutoff': 2.5
        }

    def locate_pool_area(self, frame):
        hsv = cv2.cvtColor(frame, cv2.COLOR_BGR2HSV)
        pool_mask = np.zeros(hsv.shape[:2], dtype=np.uint8)
        for r in self.pool_hsv_ranges:
            pool_mask |= cv2.inRange(hsv, r['low'], r['high'])

        # Morphological cleaning
        small = np.ones((5, 5), np.uint8)
        large = np.ones((20, 20), np.uint8)
        pool_mask = cv2.morphologyEx(pool_mask, cv2.MORPH_OPEN, small)
        pool_mask = cv2.morphologyEx(pool_mask, cv2.MORPH_CLOSE, large)

        contours, _ = cv2.findContours(pool_mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
        if contours:
            pool_mask[:] = 0
            cv2.drawContours(pool_mask, [max(contours, key=cv2.contourArea)], -1, 255, -1)
        return pool_mask

    def is_valid_detection(self, image, box, pool_mask):
        x1, y1, x2, y2 = box
        w, h = x2 - x1, y2 - y1

        if w < self.detection_rules['min_size'][0] or h < self.detection_rules['min_size'][1]:
            return False

        ar = h / w
        if not (self.detection_rules['aspect'][0] <= ar <= self.detection_rules['aspect'][1]):
            return False

        box_area = h * w
        img_area = image.shape[0] * image.shape[1]
        if not (self.detection_rules['area'][0] <= box_area / img_area <= self.detection_rules['area'][1]):
            return False

        # Check overlap with pool
        box_mask = np.zeros_like(pool_mask)
        box_mask[y1:y2, x1:x2] = 1
        overlap_ratio = np.sum(np.logical_and(pool_mask, box_mask)) / np.sum(box_mask)
        if overlap_ratio < self.detection_rules['overlap']:
            return False

        if h / w > self.detection_rules['vertical_cutoff']:
            return False

        return True

    def _link_tracks(self, detections, fid):
        centroids = [(((x1+x2)//2, (y1+y2)//2), det) for det in detections for x1, y1, x2, y2 in [det['bbox']]]
        active_tracks = {tid: t for tid, t in self.tracks.items() if fid - t['frames'][-1] <= self.track_gap}

        matched = set()
        for tid, track in active_tracks.items():
            if not centroids:
                continue
            last = track['centroids'][-1]
            distances = [np.linalg.norm(np.array(c) - np.array(last)) for c, _ in centroids]
            min_idx = np.argmin(distances)
            if distances[min_idx] < 100:
                c, d = centroids[min_idx]
                matched.add(min_idx)
                track['centroids'].append(c)
                track['frames'].append(fid)

        for i, (c, d) in enumerate(centroids):
            if i not in matched:
                self.tracks[len(self.tracks)] = {
                    'centroids': deque([c], maxlen=self.track_max_length),
                    'frames': deque([fid], maxlen=self.track_max_length)
                }

        confirmed = []
        for c, d in centroids:
            for track in self.tracks.values():
                if track['centroids'][-1] == c and len(track['frames']) >= self.track_min_length:
                    confirmed.append(d)
                    break
        return confirmed

    def detect(self, frame, fid):
        pool_mask = self.locate_pool_area(frame)
        raw_results = self.model(frame)

        valid_detections = []
        for result in raw_results:
            for box in result.boxes:
                x1, y1, x2, y2 = map(int, box.xyxy[0].cpu().numpy())
                conf = float(box.conf[0])
                cls = int(box.cls[0])

                if cls == 0 and conf >= self.conf_threshold:
                    bbox = (x1, y1, x2, y2)
                    if self.is_valid_detection(frame, bbox, pool_mask):
                        valid_detections.append({'bbox': bbox, 'confidence': conf})

        return self._link_tracks(valid_detections, fid), pool_mask

    def annotate_and_save(self, frame_path, out_dir, fid):
        frame = cv2.imread(frame_path)
        if frame is None:
            return False

        detections, pool_mask = self.detect(frame, fid)
        if not detections:
            return False

        out_img = frame.copy()
        overlay = cv2.cvtColor(pool_mask, cv2.COLOR_GRAY2BGR)
        overlay[pool_mask > 0] = (100, 100, 0)
        cv2.addWeighted(out_img, 0.7, overlay, 0.3, 0, out_img)

        timestamp = datetime.now().strftime("%Y%m%d_%H%M%S_%f")
        name = os.path.splitext(os.path.basename(frame_path))[0]
        vis_path = os.path.join(out_dir, f"detection_{timestamp}_{name}.jpg")

        h, w = frame.shape[:2]
        for i, det in enumerate(detections):
            x1, y1, x2, y2 = det['bbox']
            cv2.rectangle(out_img, (x1, y1), (x2, y2), (0, 255, 0), max(1, int(det['confidence'] * 3)))
            label = f"Swimmer {det['confidence']:.2f}"
            cv2.putText(out_img, label, (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

            # Save crop
            pad = 10
            x1p, y1p = max(0, x1 - pad), max(0, y1 - pad)
            x2p, y2p = min(w, x2 + pad), min(h, y2 + pad)
            crop = frame[y1p:y2p, x1p:x2p]
            cv2.imwrite(os.path.join(out_dir, f"swimmer_{timestamp}_{name}_{i}.jpg"), crop)

        cv2.imwrite(vis_path, out_img)
        return True

    def process_folder(self, input_dir, output_dir):
        os.makedirs(output_dir, exist_ok=True)
        imgs = sorted([f for f in os.listdir(input_dir) if f.lower().endswith(('.jpg', '.jpeg', '.png'))])

        if not imgs:
            print("No valid images found.")
            return

        print(f"\n🧠 Processing {len(imgs)} frames...")
        found, fails = 0, 0

        for fid, img in enumerate(tqdm(imgs)):
            try:
                full_path = os.path.join(input_dir, img)
                if self.annotate_and_save(full_path, output_dir, fid):
                    found += 1
            except Exception as e:
                fails += 1
                print(f"Failed on {img}: {e}")

        print("\n✅ Batch completed.")
        print(f"🖼  Total: {len(imgs)} | ✅ Detections: {found} | ❌ Errors: {fails}")

# --- Run This Script Directly ---
if __name__ == "__main__":
    detector = SwimmerTracker(model_path='yolov8x.pt', conf_thresh=0.6)

    INPUT_DIR = r"C:\Users\Jay\Desktop\CV_Project\Extracted_Frames"
    OUTPUT_DIR = r"C:\Users\Jay\Desktop\CV_Project\Swimmer_Detections"

    detector.process_folder(INPUT_DIR, OUTPUT_DIR)



🧠 Processing 12007 frames...


  0%|                                                                                        | 0/12007 [00:00<?, ?it/s]


0: 384x640 3 persons, 45.7ms
Speed: 3.1ms preprocess, 45.7ms inference, 3.3ms postprocess per image at shape (1, 3, 384, 640)


  0%|                                                                              | 1/12007 [00:01<4:55:48,  1.48s/it]


0: 384x640 6 persons, 40.7ms
Speed: 2.7ms preprocess, 40.7ms inference, 4.2ms postprocess per image at shape (1, 3, 384, 640)


...


0: 384x640 1 person, 45.0ms
Speed: 2.3ms preprocess, 45.0ms inference, 3.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 42.4ms
Speed: 2.4ms preprocess, 42.4ms inference, 3.7ms postprocess per image at shape (1, 3, 384, 640)


100%|███████████████████████████████████████████████████████████████████████████▉| 12006/12007 [22:37<00:00, 10.21it/s]


0: 384x640 1 person, 41.5ms
Speed: 2.4ms preprocess, 41.5ms inference, 3.7ms postprocess per image at shape (1, 3, 384, 640)


100%|████████████████████████████████████████████████████████████████████████████| 12007/12007 [22:37<00:00,  8.85it/s]


✅ Batch completed.
🖼  Total: 12007 | ✅ Detections: 1212 | ❌ Errors: 0
